In [1]:
import geopandas as gpd
import pandas as pd
import osmnx as ox
import matplotlib.pyplot as plt
import os
import folium
import alphashape
import numpy as np
from tqdm.notebook import tqdm
import matplotlib.animation as animation
import imageio
import networkx as nx
import io
from PIL import Image
import time
import sys
from matplotlib import cm
from IPython.display import clear_output
import seaborn as sns
import matplotlib.colors as mcolors
from shapely import box
import gc
pd.options.mode.copy_on_write = True

%matplotlib inline

In [11]:
class Network:
    def __init__(self, crs = 32618):
        self.crs = crs
        self.n_pot = None
        self.n_pot_og = None
        self.n_pot_nodes = None
        self.n_pot_edges = None
        self.n_ex = None
        self.n_ex_og = None
        self.n_ex_nodes = None
        self.n_ex_edges = None
        self.trips = None
        self.map_pot = None
        self.map_ex = None
        self.map_routes = None
        self.trips = None
        self.trips_within = None
        self.sample = None
        self.boundaries = None
        self.routes = []
        self.unsolved_routes_ids = []
        self.all_routes_edges = None
        self.routes_summary = None
        self.evol = []
        self.associated_links = None
        
    def load_n_pot(self,path):
        self.n_pot = ox.io.load_graphml(path)
        self.n_pot = ox.project_graph(self.n_pot)
        self.n_pot_nodes,self.n_pot_edges = ox.graph_to_gdfs(self.n_pot)
        cols = self.n_pot_nodes.columns
        self.n_pot_nodes = self.n_pot_nodes.sjoin(self.n_pot_edges,predicate = 'intersects', lsuffix = None)
        self.n_pot_nodes = self.n_pot_nodes[cols]
        self.n_pot_nodes = self.n_pot_nodes.drop_duplicates()
        self.n_pot_edges['build_iter'] = 0
        self.n_pot_og = ox.graph_from_gdfs(self.n_pot_nodes.copy(),self.n_pot_edges.copy())
        
    def filter_n_pot(self):
        self.n_pot_edges[self.n_pot_eges.highway.isin(['residential','primary','secondary','tertiary','tertiary_link'])]
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)

    def plot_n_pot(self, nodes = False):
        if self.n_pot == None:
            print('No potential network loaded')
        else:
            self.map_pot = self.n_pot_edges.explore(color = 'black')
            if nodes:
                self.n_pot_nodes.explore(m = self.map_pot)
            display(self.map_pot)

    def load_n_ex(self,path):
        self.n_ex = ox.io.load_graphml(path)
        self.n_ex = ox.project_graph(self.n_ex)
        self.n_ex_nodes,self.n_ex_edges = ox.graph_to_gdfs(self.n_ex)
        cols = self.n_ex_nodes.columns
        self.n_ex_nodes = self.n_ex_nodes.sjoin(self.n_ex_edges,predicate = 'intersects', lsuffix = None)
        self.n_ex_nodes = self.n_ex_nodes[cols]
        self.n_ex_nodes = self.n_ex_nodes.drop_duplicates()
        self.n_ex_edges['build_iter'] = 0
        self.n_ex_og = ox.graph_from_gdfs(self.n_ex_nodes.copy(),self.n_ex_edges.copy())

    def filter_n_ex(self,highway_type = 'cycleway'):
        self.n_ex_edges = self.n_ex_edges[self.n_ex_edges.highway == highway_type]
        self.n_ex = ox.graph_from_gdfs(self.n_ex_nodes,self.n_ex_edges)

    def plot_n_ex(self, nodes = False):
        if self.n_ex == None:
            print('No existing network loaded')
        else:
            self.map_ex = self.n_ex_edges.explore(color = 'black')
            if nodes:
                self.n_ex_nodes.explore(m = self.map_ex)
            display(self.map_ex)

    def load_trips(self, path, cols = ['ipere','mode','motif','age','xorig','yorig','xdest','ydest','potVelo','fexpPotVelo', 'velo'],potvel = True):
        self.trips = pd.read_csv(path)
        if potvel == True:
            self.trips = self.trips[self.trips.potVelo == 1]
        self.trips = self.trips[cols]
        self.trips = gpd.GeoDataFrame(self.trips, geometry=gpd.points_from_xy(self.trips.xorig, self.trips.yorig), crs=32188)
        self.trips = self.trips.rename(columns = {'geometry': 'orig'})
        self.trips = self.trips.assign(dest = gpd.points_from_xy(self.trips.xdest, self.trips.ydest,crs=32188))
        self.trips = self.trips.set_geometry('orig')
        self.trips = self.trips.to_crs(self.crs)
        self.boundaries = gpd.GeoDataFrame({'name':['region']},geometry = gpd.GeoSeries(self.n_pot_edges.geometry.union_all()).concave_hull(0.2)
                                           , crs = self.crs)
        
        self.trips = self.trips.to_crs(self.crs)
        self.trips.index+=1
        self.trips_within = gpd.sjoin(self.trips, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]
        self.trips_within = self.trips_within.set_geometry('dest')
        self.trips_within = self.trips_within.to_crs(self.crs)
        self.trips_within = gpd.sjoin(self.trips_within, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]
        


    def sample_trips(self,sample_size = None, spec_route = None):
        if sample_size is None:
            sample_size = len(self.trips_within)
            self.sample = self.trips_within.sample(sample_size)
        else:
            self.sample = pd.concat([self.sample,self.trips_within.sample(sample_size)])
        if spec_route is not None:
            self.sample = self.trips_within[self.trips_within.ipere == spec_route]

    def compute_routes(self, network, weight = 'gencost'):
        network = ox.projection.project_graph(network, to_crs = self.crs)
        o_nodes,o_dists = ox.nearest_nodes(network,self.sample.orig.x.values,self.sample.orig.y.values, return_dist=True)
        d_nodes,d_dists = ox.nearest_nodes(network,self.sample.dest.x.values,self.sample.dest.y.values, return_dist=True)
        routes = ox.shortest_path(network, o_nodes, d_nodes, weight=weight,cpus = None)
        self.routes+=routes

    
    def reset_sample(self):
        self.sample = None
    def reset_routes(self):
        self.routes = []
        self.unsolved_routes_ids = []
        self.all_routes_edges = None
        self.routes_summary = None
        
    def get_routes_edges(self,network):
        route_edges = []
        static_route_ids = []
        for i in tqdm(range(len(self.routes)),leave = False):
            if self.routes[i] is not None:
                if len(self.routes[i])>1:
                    edges = ox.routing.route_to_gdf(network,self.routes[i])
                    edges['route_number'] = self.sample.index[i]
                    route_edges.append(edges) 
                else:
                    static_route_ids.append(self.sample.index[i])
            
            else:
                self.unsolved_routes_ids.append(self.sample.index[i])
                continue
        print((1-len(self.unsolved_routes_ids)/len(self.sample))*100,'% of solved routes, ',len(static_route_ids)/len(self.sample)*100,
        ' % of static routes')
        self.sample = self.sample.drop(self.unsolved_routes_ids)
        self.sample = self.sample.drop(static_route_ids)
        self.all_routes_edges = pd.concat(route_edges)
    
    def compute_routes_summary(self):
        
        self.routes_summary = self.all_routes_edges[['length','gencost','route_number']].groupby(['route_number']).sum()
        self.routes_summary['length_cycleway'] = self.all_routes_edges.groupby('route_number').apply(
            lambda x: x.loc[x["highway"] == "cycleway", "length"].sum(),include_groups=False)
        self.routes_summary['length_street'] = self.all_routes_edges.groupby('route_number').apply(
            lambda x: x.loc[x["highway"] != "cycleway", "length"].sum(),include_groups=False)
        self.routes_summary['prop_cycleway'] = self.routes_summary['length_cycleway']/self.routes_summary['length']

        # links = self.all_routes_edges[self.all_routes_edges.highway !='cycleway'].drop_duplicates()
        # flows = self.all_routes_edges[self.all_routes_edges.highway !='cycleway'].groupby(by = ['length'], as_index = False).size()['size']
        # links['flow'] = flows.values
        # links['flux'] = flows.values*links.length

    def plot_routes(self,network):

        if self.all_routes_edges is None:
            self.get_routes_edges(network)
        

        self.sample = self.sample.set_geometry('orig')
        self.map_routes = self.sample.explore(color='blue', name='orig')
        self.sample = self.sample.set_geometry('dest')
        map2 = self.sample.explore(color='red', name='dest', m=self.map_routes)
        map3 = self.boundaries.explore(m = self.map_routes, name = 'boundaries', fill = False)
        map4 = self.n_ex_edges.explore(color='black', name='existing', m=self.map_routes,style_kwds={'opacity': 0.3})
        map5 = self.n_pot_edges.explore(color='black', name='potential', m=self.map_routes,style_kwds={'opacity': 0.3})
        self.all_routes_edges['route_n'] = self.all_routes_edges['route_number'].astype(str)
        map8 = self.all_routes_edges.explore(column = 'route_n',cmap = 'gist_rainbow', name = 'routes', m = self.map_routes, legend = False
                                            ,style_kwds={'weight': 5})
        folium.LayerControl().add_to(self.map_routes)
        display(self.map_routes)

    def weight_network(self,cycleway_reduc_factor=0.9):
        self.n_pot_edges['gencost'] = self.n_pot_edges["length"] * self.n_pot_edges["highway"].apply(
            lambda x: cycleway_reduc_factor if x == "cycleway" else 1)
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)


    def compute_routes_replace(self,network,idxs,weight = 'gencost'):
        network = ox.projection.project_graph(network, to_crs = self.crs)
        subsample = self.sample.loc[idxs]
        o_nodes,o_dists = ox.nearest_nodes(network,subsample.orig.x.values,subsample.orig.y.values, return_dist=True)
        d_nodes,d_dists = ox.nearest_nodes(network,subsample.dest.x.values,subsample.dest.y.values, return_dist=True)
        routes = ox.shortest_path(network, o_nodes, d_nodes, weight=weight)
        route_edges = []
        for i in range(len(idxs)):
                if routes[i] is not None:
                    if len(routes[i])>1:
                        edges = ox.routing.route_to_gdf(network,routes[i])
                        edges['route_number'] = idxs[i]
                        route_edges.append(edges)
        newroutes = pd.concat(route_edges)
        self.all_routes_edges = self.all_routes_edges[~self.all_routes_edges['route_number'].isin(idxs)]
        self.all_routes_edges = pd.concat([self.all_routes_edges,newroutes])
        
    def run_algo(self,n_iter = 1000, budget = 10000):
        self.reset_routes()
        self.compute_routes(self.n_pot)
        self.get_routes_edges(self.n_pot)
 
        for i in tqdm(range(n_iter)):
            clear_output(wait = True)
            self.compute_routes_summary()
            preconnected = self.routes_summary[(self.routes_summary['length_cycleway']>0)&(self.routes_summary['length_street']>0)]
            route_id_to_add = preconnected[preconnected['length_street'] == preconnected['length_street'].min()].index[0]
            print('adding ',route_id_to_add)
            route_edges = self.all_routes_edges[self.all_routes_edges.route_number == int(route_id_to_add)]
            route_edges_to_add = route_edges[route_edges.highway!='cycleway']
    
            edges_id_to_add = route_edges_to_add.index
            self.n_pot_edges.loc[edges_id_to_add,'highway']='cycleway'
            self.n_pot_edges.loc[edges_id_to_add,'build_iter'] = np.max(self.n_pot_edges.build_iter)+1
            self.n_ex_edges = self.n_pot_edges[self.n_pot_edges.highway == 'cycleway']
    
            self.weight_network()
            self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)
    
            recompute_polygon = route_edges.buffer(500).union_all()
            recompute_polygon = gpd.GeoDataFrame([recompute_polygon]).rename(columns={0:'geometry'}).set_geometry('geometry')
            recompute_polygon = recompute_polygon.set_crs(self.crs)
            
            o_int = recompute_polygon.sjoin(self.sample.set_geometry('orig')).index_right.tolist()
            d_int = recompute_polygon.sjoin(self.sample.set_geometry('dest')).index_right.tolist()
    
            recompute_idxs = list(set(o_int+d_int))

            m = recompute_polygon.explore()
            self.sample.loc[o_int].explore(m = m, color = 'yellow')
            display(m)
            break
    
            if len(recompute_idxs) == 0:
                continue
            else:
                print('recomputing ',len(recompute_idxs))
                self.compute_routes_replace(self.n_pot,recompute_idxs)
            

In [123]:
n = Network()
ex = 'Data/Reseaux/ns_EX_MTLCENTRE.graphml'
pot = 'Data/Reseaux/ns_POT_MTLCENTRE.graphml'
# ex = 'Data/Reseaux/ns_EX_Laval,Qc.graphml'
# pot = 'Data/Reseaux/ns_POT_Laval,Qc.graphml'
trips = 'Data/od18_extraqit_20250123/od18_extraqit_20250123.csv'

In [124]:
n.load_n_pot(pot)
n.load_n_ex(ex)
n.load_trips(trips)

In [200]:
def funcToMethod(func, clas, method_name=None):
    setattr(clas, method_name or func.__name__, func)
def run_algo(self, budget,n_iter = 1000,plot = True):
    if np.max(self.n_pot_edges.build_iter) == 0:
        self.reset_routes()
        self.evol = []
        self.compute_routes(self.n_pot)
        self.get_routes_edges(self.n_pot)
        self.compute_routes_summary()
        self.evol.append(self.routes_summary.copy().prop_cycleway)
    while self.n_ex_edges[self.n_ex_edges.build_iter > 0].length.sum()/1000 < budget:
        if plot:
            if i==0:
                fig, ax = plt.subplots(figsize = (5,5))
                ax.axis('off')
        clear_output(wait = True)
        print(f'Iteration {self.n_ex_edges[self.n_ex_edges.build_iter > 0].length.sum()/1000}/'+str(budget))
        preconnected = self.routes_summary[(self.routes_summary['length_cycleway']>0)&(self.routes_summary['length_street']>0)]
        if len(preconnected) == 0 and i<len(self.sample):
            preconnected = self.routes_summary[(self.routes_summary['length_street']>0)]
        route_id_to_add = preconnected.sort_values(by = 'fpkm', ascending = False).index[0]
        print(self.routes_summary.loc[route_id_to_add])
        recompute_summary_idxs = preconnected.sort_values(by = 'fpkm', ascending = False).index[:len(self.routes_summary)//10+1].tolist()
        
        
        route_edges = self.all_routes_edges[self.all_routes_edges.route_number == int(route_id_to_add)]
        route_edges_to_add = route_edges[route_edges.highway!='cycleway']

        edges_id_to_add = route_edges_to_add.index
        self.n_pot_edges.loc[edges_id_to_add,'highway']='cycleway'
        self.n_pot_edges.loc[edges_id_to_add,'build_iter'] = np.max(self.n_pot_edges.build_iter)+1
        self.n_ex_edges = self.n_pot_edges[self.n_pot_edges.highway == 'cycleway']
        self.all_routes_edges.loc[edges_id_to_add,'highway']='cycleway'

        self.compute_routes_summary(subsample_idxs = recompute_summary_idxs)
        self.evol.append(self.routes_summary.copy()['prop_cycleway'])
        if plot:
            if i%5== 0:
                
                n.n_ex_edges[n.n_ex_edges.build_iter<=i].plot(column = 'build_iter',cmap = 'viridis',ax=ax)
                clear_output(wait = True)
                display(fig)
                print(f'Iteration {i}/{n_iter}')



def compute_routes_summary(self, subsample_idxs = None):
    if subsample_idxs is None:
        subsample = self.all_routes_edges
        subsample_idxs = self.sample.index
        self.routes_summary = subsample[['length','gencost','route_number']].groupby(['route_number']).sum()
    else:
        subsample = self.all_routes_edges[self.all_routes_edges.route_number.isin(subsample_idxs)]
        
    
    self.routes_summary.loc[subsample_idxs,'length_cycleway'] = subsample.groupby('route_number').apply(
        lambda x: x.loc[x["highway"] == "cycleway", "length"].sum(),include_groups=False)
    self.routes_summary.loc[subsample_idxs,'length_street'] = subsample.groupby('route_number').apply(
        lambda x: x.loc[x["highway"] != "cycleway", "length"].sum(),include_groups=False)
    self.routes_summary.loc[subsample_idxs,'prop_cycleway'] = (self.routes_summary.loc[subsample_idxs,'length_cycleway']/
                                                                self.routes_summary.loc[subsample_idxs,'length'])
    subsample['flow'] = subsample.join(subsample.index.value_counts(), how = 'left')['count']
    self.routes_summary.loc[subsample_idxs,'fpkm'] = subsample.groupby('route_number').apply(
        lambda x: ((x.loc[x["highway"] != "cycleway", "flow"]*
                   x.loc[x["highway"] != "cycleway", "length"]).sum()/x.loc[x["highway"] != "cycleway", "length"].sum())
        if x.loc[x["highway"] != "cycleway", "length"].sum() != 0 else 0 ,include_groups=False)
    self.routes_summary.loc[subsample_idxs,'tort'] = self.routes_summary.loc[subsample_idxs,'length']/self.sample.loc[subsample_idxs,'orig'].distance(self.sample.loc[subsample_idxs,'dest'])


def compute_routes_replace(self,network,idxs,weight = 'gencost'):
    # network = ox.projection.project_graph(network, to_crs = self.crs)
    subsample = self.sample.loc[idxs]
    o_nodes,o_dists = ox.nearest_nodes(network,subsample.orig.x.values,subsample.orig.y.values, return_dist=True)
    d_nodes,d_dists = ox.nearest_nodes(network,subsample.dest.x.values,subsample.dest.y.values, return_dist=True)
    routes = ox.shortest_path(network, o_nodes, d_nodes, weight=weight,cpus=None)
    route_edges = []
    for i in tqdm(range(len(idxs)),leave = False):
            if routes[i] is not None:
                if len(routes[i])>1:
                    edges = ox.routing.route_to_gdf(network,routes[i])
                    edges['route_number'] = idxs[i]
                    route_edges.append(edges)
    newroutes = pd.concat(route_edges)
    self.all_routes_edges = self.all_routes_edges[~self.all_routes_edges['route_number'].isin(idxs)]
    self.all_routes_edges = pd.concat([self.all_routes_edges,newroutes])
def reset_network(self):
    self.n_ex = self.n_ex_og.copy()
    self.n_ex_nodes,self.n_ex_edges = ox.graph_to_gdfs(self.n_ex)
    self.n_pot = self.n_pot_og.copy()
    self.n_pot_nodes,self.n_pot_edges = ox.graph_to_gdfs(self.n_pot)

def simulate_demand(self, size, method = 'uniform', max_dist = 5000):
    self.boundaries = gpd.GeoDataFrame({'name':['region']},geometry = gpd.GeoSeries(self.n_pot_edges.geometry.union_all()).concave_hull(0.2)
                                           , crs = self.crs)
    points = gpd.GeoDataFrame(self.boundaries.sample_points(size = size,method = method))
    points = points.set_geometry('sampled_points')
    points = points.explode()
    dests = []
    for point in points.sampled_points:
        circle = gpd.GeoDataFrame({'geometry':[point.buffer(max_dist)]}).set_crs(self.crs)
        dest_poly = gpd.overlay(circle,self.boundaries).geometry
        dest = dest_poly.sample_points(size=1).geometry.iloc[0]
        dests.append(dest)
    dests_gdf = gpd.GeoDataFrame({'geometry':dests}).set_crs(self.crs)

    self.sample = points
    self.sample = pd.concat([self.sample.reset_index(drop = True),dests_gdf.reset_index(drop = True)], axis = 1)
    self.sample = self.sample.rename(columns = {'sampled_points':'orig','geometry':'dest'})

def run_algo2(self, budget,plot = True, buffer = 350, buffer_int_prop = .5, cost_reduction_factor=0.9):
    added_routes = []
    i=0
    if np.max(self.n_pot_edges.build_iter) == 0:
        self.od_bbox(buffer = buffer)
        self.reset_routes()
        self.evol = []
        self.compute_routes(self.n_pot)
        self.get_routes_edges(self.n_pot)
        self.compute_routes_summary()
        self.evol.append(self.routes_summary.copy())
    else:
        i=np.max(self.n_pot_edges.build_iter)
    while self.n_ex_edges[self.n_ex_edges.build_iter > 0].length.sum()/1000 < budget:
        if plot:
            if i==0:
                fig, ax = plt.subplots(figsize = (5,5))
                ax.axis('off')
        clear_output(wait = True)
        print(f'Built {self.n_ex_edges[self.n_ex_edges.build_iter > 0].length.sum()/1000}/{str(budget)} km (iteration {i})')
        preconnected = self.routes_summary[(self.routes_summary['length_cycleway']>0)&(self.routes_summary['length_street']>0)]
        if len(preconnected) == 0 and i<len(self.sample):
            preconnected = self.routes_summary[(self.routes_summary['length_street']>0)]
        route_id_to_add = preconnected.sort_values(by = 'fpkm', ascending = False).index[0]
        print(route_id_to_add)
        route_edges = self.all_routes_edges[self.all_routes_edges.route_number == int(route_id_to_add)]
        route_edges_to_add = route_edges[route_edges.highway!='cycleway']

        edges_id_to_add = route_edges_to_add.index
        self.n_pot_edges.loc[edges_id_to_add,'highway']='cycleway'
        self.n_pot_edges.loc[edges_id_to_add,'build_iter'] = np.max(self.n_pot_edges.build_iter)+1
        self.n_ex_edges = self.n_pot_edges[self.n_pot_edges.highway == 'cycleway']
        self.all_routes_edges.loc[edges_id_to_add,'highway']='cycleway'

        self.weight_network(cost_reduction_factor)
        routes_int_idxs = self.associated_links.loc[edges_id_to_add].values
        routes_int_idxs = list(set(routes_int_idxs) & set(self.sample.index.values))
   
        added_routes.append(route_id_to_add)
        self.evol.append(self.routes_summary.copy())
        if len(routes_int_idxs) == 0:
            self.compute_routes_replace(self.n_pot,[route_id_to_add])
        else:
            print('recomputing ',len(routes_int_idxs)/len(self.sample),f'({len(routes_int_idxs)}/{len(self.sample)})')
            self.compute_routes_replace(self.n_pot,list(set(routes_int_idxs)-set(added_routes)))
        
        self.compute_routes_summary(subsample_idxs = list(set(routes_int_idxs)|set([route_id_to_add])))
        i+=1
        
def od_bbox(self,buffer):

    def compute_bounding_box(row):
        min_x = min(row["orig"].x, row["dest"].x)
        max_x = max(row["orig"].x, row["dest"].x)
        min_y = min(row["orig"].y, row["dest"].y)
        max_y = max(row["orig"].y, row["dest"].y)
        return box(min_x, min_y, max_x, max_y).buffer(buffer)
        

    def get_links_bbox(row):
        links = gpd.sjoin(row,self.n_pot_edges,how = 'left',
                          predicate = 'intersects').set_index(['u', 'v', 'key'])['ipere']
        return links
    n_pot_unproj = ox.projection.project_graph(self.n_pot,to_crs=4326)
    n_pot_angle = ox.bearing.add_edge_bearings(ox.convert.to_undirected(n_pot_unproj))
    nodes,edges = ox.graph_to_gdfs(n_pot_angle)
    edges = edges.dropna(subset=['bearing'])    
    lengths = pd.merge(edges,self.n_pot_edges,how = 'inner')['length']
    dom_angle = np.average(edges.bearing.values%90,weights = lengths.values)
    dom_angle = 0
    centroid = self.sample.union_all().centroid
    rotated_sample_o = self.sample.orig.rotate(dom_angle,centroid).explode()
    rotated_sample_d = self.sample.dest.rotate(dom_angle,centroid).explode()
    rotated_sample_o.name = 'orig'
    rotated_sample_d.name = 'dest'
    rotated_sample = pd.concat([rotated_sample_o,rotated_sample_d],axis = 1)
    rotated_sample = gpd.GeoDataFrame(rotated_sample,geometry='orig')
    rotated_sample["bbox"] = rotated_sample.apply(compute_bounding_box, axis=1)
    rotated_sample.set_crs(self.crs)
    self.sample['bbox'] = rotated_sample.bbox.rotate(-dom_angle,centroid)
    self.sample = self.sample.set_geometry('bbox').set_crs(self.crs)
    self.associated_links = gpd.sjoin(self.sample,self.n_pot_edges,how = 'left',
                          predicate = 'intersects').set_index(['u', 'v', 'key'])['ipere']
def weight_network(self,cycleway_reduc_factor=0.9):
    self.n_pot_edges['gencost'] = self.n_pot_edges["length"] * self.n_pot_edges["highway"].apply(
        lambda x: cycleway_reduc_factor if x == "cycleway" else 1)
    self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)
        
funcToMethod(run_algo,Network,method_name = 'run_algo')
funcToMethod(compute_routes_summary,Network,method_name = 'compute_routes_summary')
funcToMethod(compute_routes_replace,Network,method_name = 'compute_routes_replace')
funcToMethod(reset_network,Network,method_name = 'reset_network')
funcToMethod(simulate_demand,Network,method_name = 'simulate_demand')
funcToMethod(run_algo2,Network,method_name = 'run_algo2')
funcToMethod(od_bbox,Network,method_name = 'od_bbox')
funcToMethod(weight_network,Network,method_name = 'weight_network')


In [ ]:
img_data = m._to_png(1)
img = Image.open(io.BytesIO(img_data))
img.save(f'Figures/donnes.png')

In [184]:
cost_reduction_factor = 0.35
np.random.seed(1991)
n.reset_network()
n.reset_routes()
n.weight_network(cycleway_reduc_factor=cost_reduction_factor)
n.reset_sample()
n.trips_within = n.trips_within[n.trips_within['mode']!='TC']
n.sample_trips(sample_size=1)

In [188]:
n.od_bbox(buffer = 500)

In [189]:
m = n.sample.bbox.explore()
n.n_pot_edges.loc[n.associated_links.index].explore(m=m,color = 'black')
n.sample.orig.explore(m=m,color = 'red')
n.sample.dest.explore(m=m,color = 'red')
display(m)

In [201]:
cost_reduction_factor = 0.5
# n.reset_network()
# n.reset_routes()
# n.weight_network(cycleway_reduc_factor=cost_reduction_factor)
# n.reset_sample()
# n.trips_within = n.trips_within[n.trips_within['mode']!='TC']
# n.sample_trips(sample_size=5000)
n.run_algo2(budget = 200,plot = False, buffer = 100, buffer_int_prop = 0.5, cost_reduction_factor = cost_reduction_factor)

Built 19.32323815826131/200 km (iteration 24)
319150
EPSG:32618
recomputing  0.044730392156862746 (219/4896)


KeyboardInterrupt: 

In [202]:
new_network = n.n_ex_edges[n.n_ex_edges.build_iter>0].explore(column = 'build_iter',cmap = 'viridis_r',style_kwds = {'weight':5})
n.n_ex_edges[n.n_ex_edges.build_iter==0].explore(color = 'red',style_kwds = {'weight':3,'opacity':0.5},m = new_network)
display(new_network)

In [ ]:
img_data = new_network._to_png(1)
img = Image.open(io.BytesIO(img_data))
img.save(f'Figures/MTLCENTRE200_R035.png')

In [ ]:
fig, ax = plt.subplots(1,3, figsize = (14,5))
cmap = plt.get_cmap('viridis')
means = []
completes = []
length = np.cumsum(n.n_ex_edges[['length','build_iter']].groupby(by = 'build_iter').sum().values)/1000
for i in range(0,len(n.evol)):
    color = cmap(i / len(n.evol))
    if i!=0:
        if (n.evol[i].prop_cycleway.mean()-n.evol[i-1].prop_cycleway.mean())>0:
            means.append(n.evol[i].prop_cycleway.mean())
            completes.append(len(n.evol[i][n.evol[i].prop_cycleway>0.9999999999999])/len(n.evol[i]))
        else:
            pass
    
    # if i in ([0,len(n.evol)-1,40,len(n.evol)-100]):
    #     sns.kdeplot(n.evol[i].prop_cycleway, clip = (0,1), fill = 0.3,ax=ax[2])

ax[2].legend(title = 'Length of existing\nnetwork (km)',labels = [round(length[0],2),round(length[40],2),round(length[-100],2),round(length[-1],2)])
ax[0].plot(length,means[:-1])
ax[1].plot(length,completes[:-1])
ax[0].set_ylabel('Mean fraction of routes on separated cycling infrastructure')
ax[0].set_xlabel('Length of existing network (km)')
ax[1].set_xlabel('Length of existing network (km)')
ax[0].set_xlabel('Length of existing network (km)')
ax[1].set_ylabel('Fraction of realizable trips')
ax[2].set_xlabel('Fraction of route on separated cycling infrastructure')
ax[2].set_ylabel('Density')
fig.tight_layout()
fig.savefig('Figures/MTLCENTRE200_R_035evol.png')

In [ ]:
new_network.save('Figures/MTLCENTRE200_R_035.html')

In [ ]:
for i in tqdm(range(0,np.max(n.n_ex_edges.build_iter))):
    new_network = n.n_ex_edges[n.n_ex_edges.build_iter<=i].explore(column = 'build_iter',style_kwds = {'weight':5})
    img_data = new_network._to_png(1)
    img = Image.open(io.BytesIO(img_data))
    img.save(f'Figures/anim_colloque/growth_{i}.png')


In [ ]:
path = 'Figures/anim_colloque/'
filenames = os.listdir(path)
filenames = sorted(filenames, key=lambda x: int(x.split('_')[1].split('.')[0]))
filenames
images = []
for filename in filenames:
    images.append(imageio.imread(path+filename))
imageio.mimsave('Figures/anim_colloque.gif', images ,fps = 15)

In [ ]:
fig, ax = plt.subplots()
ax.axis('off')
for i in tqdm(range(0,np.max(n.n_ex_edges.build_iter))):
    ax.clear()  # Clear the axis
    ax.axis('off')
    n.n_ex_edges[n.n_ex_edges.build_iter<=i].plot(column = 'build_iter',cmap = 'viridis',ax=ax)
    fig.savefig(f'Figures/growth_RVP2/growth_{i}.png')

In [ ]:
fig, ax = plt.subplots()
hist = ax.hist(n.trips_within.motif,bins = np.arange(0.5,7.5,1))[0]

In [ ]:
print(hist[2],np.sum(hist)-hist[2])

In [ ]:
n.n_pot_edges[n.n_pot_edges.highway!='cycleway'].length.sum()

In [ ]:
n.n_pot_edges.explore()

In [ ]:
n.trips_within

In [ ]:
n_motor = Network()
n_motor.load_n_ex(ex)
n_motor.load_n_pot(pot)
n_motor.load_trips(trips)

In [ ]:
n_motor.trips_within = n_motor.trips_within[n_motor.trips_within['mode'] != 'TC']

In [ ]:
n_motor.reset_network()
n_motor.reset_routes()
n_motor.weight_network(cycleway_reduc_factor=0.9)
n_motor.reset_sample()
n_motor.sample_trips()
n_motor.run_algo(budget = 105,plot = False)

In [ ]:
n_minors = Network()
n_minors.load_n_ex(ex)
n_minors.load_n_pot(pot)
n_minors.load_trips(trips)
n_minors.trips_within = n_minors.trips_within[n_minors.trips_within['age'] < 18]

In [ ]:
n_minors.reset_network()
n_minors.reset_routes()
n_minors.weight_network(cycleway_reduc_factor=0.9)
n_minors.reset_sample()
n_minors.sample_trips()
n_minors.run_algo(budget = 105,plot = False)

In [ ]:
n_cyclists = Network()
n_cyclists.load_n_ex(ex)
n_cyclists.load_n_pot(pot)
n_cyclists.load_trips(trips,potvel=False)
n_cyclists.trips_within = n_cyclists.trips_within[n_cyclists.trips_within['velo'] == 'X']

In [ ]:
n_cyclists.reset_network()
n_cyclists.reset_routes()
n_cyclists.weight_network(cycleway_reduc_factor=0.9)
n_cyclists.reset_sample()
n_cyclists.sample_trips()
n_cyclists.run_algo(budget = 105,plot = False)

In [ ]:
networks = [n_motor,n_minors,n_cyclists]
scenarios = ['Motorized','Minors','Cyclists']
fig, ax = plt.subplot_mosaic(np.array([[0,0,0],[1,1,1],[2,3,4]]).T,figsize = (12,4))

cmap = plt.get_cmap('viridis_r')
for j, net in enumerate(networks):
    means = []
    completes = []
    length = np.cumsum(net.n_ex_edges[['length','build_iter']].groupby(by = 'build_iter').sum().values)/1000
    for i in range(0,len(net.evol)):
        color = cmap(i / len(net.evol))
        means.append(net.evol[i].mean())
        completes.append(len(net.evol[i][net.evol[i]>0.9999999999999]))
    sns.kdeplot(net.evol[0], cut = 0, fill = 0.3,color = cmap(0),ax=ax[j+2], label = 'First iteration')
    sns.kdeplot(net.evol[-1], cut = 0, fill = 0.3,color = cmap(np.inf),ax=ax[j+2], label = 'Last iteration')
    ax[1].plot(length,means)
    ax[0].plot(length,completes, label = scenarios[j])


# ax[2].legend(title = 'Length of existing\nnetwork (km)')
ax[1].set_ylabel('Mean fraction of routes on separated\ncycling infrastructure')
ax[0].set_xlabel('Length of existing network (km)')
ax[1].set_xlabel('Length of existing network (km)')
ax[0].set_xlabel('Length of existing network (km)')
ax[0].set_ylabel('Number of feasible trips')
ax[4].set_xlabel('Fraction of distance travelled on separated\ncycling infrastructure')
ax[3].set_ylabel('Minors')
ax[0].legend(title = 'Scenario')
ax[2].set_xlabel(None)
ax[3].set_xlabel(None)
ax[2].set_ylabel('Motorized')
ax[2].set_title('Distributions')
ax[4].set_ylabel('Cyclists')
ax[2].sharey(ax[3])
ax[4].sharey(ax[3])
fig.tight_layout()
ax[2].legend(fontsize = 8)
fig.savefig('Figures/CTRF/metrics.png')

In [ ]:
for net in networks:
    print(net.evol[0].mean())
    print(len(net.evol))

In [ ]:
len(length)

In [ ]:
n.n_pot_edges